## Section 7.1: A First Plotly Streaming Plot

Welcome to Plotly's Python API User Guide. 

> Links to the other sections can be found on the User Guide's [homepage](https://plotly.com/python/user-guide#Table-of-Contents:) 

Section 7 is divided, into separate notebooks, as follows:

* [7.0 Streaming API introduction](https://plotly.com/python/intro_streaming)

* [7.1 A First Plotly Streaming Plot](https://plotly.com/python/streaming_part1)

<hr>

Check which version is installed on your machine and please upgrade if needed. 

In [1]:
# (*) Import plotly package
import plotly
 
# Check plolty version (if not latest, please upgrade)
plotly.__version__

'1.9.5'

<hr>

Import a few modules and sign in to Plotly using our credentials file:

In [3]:
# (*) To communicate with Plotly's server, sign in with credentials file
import plotly.plotly as py  
 
# (*) Useful Python/Plotly tools
import plotly.tools as tls   
 
# (*) Graph objects to piece together plots
from plotly.graph_objs import *
 
import numpy as np  # (*) numpy for math functions and arrays

Finally, retrieve the stream ids in our credentials file as set up in <a href="https://plotly.com/python/streaming-tutorial#Get-your-stream-tokens" target="_blank">subsection 7.1</a>:

In [6]:
stream_ids = tls.get_credentials_file()['stream_ids']

### 7.1 A first Plotly streaming plot

Making Plotly streaming plots sums up to working with two objects:

* A stream id object (`Stream` in the `plotly.graph_objs` module),

* A stream link object (`py.Stream`).

The stream id object is a graph object that embeds a particular stream id to each of your plot's traces. As all graph objects, the stream id object is equipped with extensive `help()` documentation, key validation and a nested update method. In brief, the stream id object initializes the connection between a trace in your Plotly graph and a data stream(for that trace).

Meanwhile, the stream link object, like all objects in the `plotly.plotly` module, links content in your Python/IPython session to Plotly's servers. More precisely, it is the interface that updates the data in the plotted traces in real-time(as identified with the unique stream id used in the corresponding stream id object).

If you find the `Stream`/`py.Stream` terminalogy too confusing --- and you do not mind not having access to the methods associated with Plotly graph objects' --- you can forgo the use of the stream id object and substitute it by a python `dict()` in the following examples. 

So, we start by making an instance of the stream id object:

In [4]:
help(Stream)  # call help() to see the specifications of the Stream object!

Help on class Stream in module plotly.graph_objs.graph_objs:

class Stream(PlotlyDict)
 |  Valid attributes for 'stream' at path [] under parents ():
 |  
 |      ['token', 'maxpoints']
 |  
 |  Run `<stream-object>.help('attribute')` on any of the above.
 |  '<stream-object>' is the object at []
 |  
 |  Method resolution order:
 |      Stream
 |      PlotlyDict
 |      __builtin__.dict
 |      PlotlyBase
 |      __builtin__.object
 |  
 |  Methods inherited from PlotlyDict:
 |  
 |  __copy__(self)
 |  
 |  __deepcopy__(self, memodict={})
 |  
 |  __dir__(self)
 |      Dynamically return the existing and possible attributes.
 |  
 |  __getattr__(self, key)
 |      Python only calls this when key is missing!
 |  
 |  __getitem__(self, key)
 |      Calls __missing__ when key is not found. May mutate object.
 |  
 |  __init__(self, *args, **kwargs)
 |  
 |  __missing__(self, key)
 |      Mimics defaultdict. This is called from __getitem__ when key DNE.
 |  
 |  __setattr__(self, key, val

In [ ]:
# Get stream id from stream id list 
stream_id = stream_ids[0]

# Make instance of stream id object 
stream = Stream(
    token=stream_id,  # (!) link stream id to 'token' key
    maxpoints=80      # (!) keep a max of 80 pts on screen
)

The `'maxpoints'` key set the maxiumum number of points to keep on the plot from an incoming stream.

Streaming Plotly plots are initialized with a standard (i.e. REST API) call to `py.plot()` or `py.iplot()` that embeds your unique stream ids in each of the plot's traces. 

Each Plotly trace object (e.g. `Scatter`, `Bar`, `Histogram`, etc. More in <a href="https://plotly.com/python/overview#0.4-Plotly's-graph-objects" target="_blank">Section 0</a>) has a `'stream'` key made available to link the trace object in question to a corresponding stream object.

In our first example, we link a scatter trace object to the stream:

In [6]:
# Initialize trace of streaming plot by embedding the unique stream_id
trace1 = Scatter(
    x=[],
    y=[],
    mode='lines+markers',
    stream=stream         # (!) embed stream id, 1 per trace
)

data = Data([trace1])

Then, add a title to the layout object and initialize your Plotly streaming plot:

In [7]:
# Add title to layout object
layout = Layout(title='Time Series')

# Make a figure object
fig = Figure(data=data, layout=layout)

# (@) Send fig to Plotly, initialize streaming plot, open new tab
unique_url = py.plot(fig, filename='s7_first-stream')

Great! Your Plotly streaming plot is intialized. Here's a screenshot:

<img src="http://i.imgur.com/Lx7ICLI.png" />

<br>

Now, let's add data on top of it, or more precisely, send a *stream* of data to it. 

So, first

In [8]:
help(py.Stream)  # run help() of the Stream link object

Help on class Stream in module plotly.plotly.plotly:

class Stream
 |  Interface to Plotly's real-time graphing API.
 |  
 |  Initialize a Stream object with a stream_id
 |  found in https://plotly.com/settings.
 |  Real-time graphs are initialized with a call to `plot` that embeds
 |  your unique `stream_id`s in each of the graph's traces. The `Stream`
 |  interface plots data to these traces, as identified with the unique
 |  stream_id, in real-time.
 |  Every viewer of the graph sees the same data at the same time.
 |  
 |  View examples and tutorials here:
 |  https://plotly.com/python/streaming/
 |  
 |  Stream example:
 |  # Initialize a streaming graph
 |  # by embedding stream_id's in the graph's traces
 |  import plotly.plotly as py
 |  from plotly.graph_objs import Data, Scatter, Stream
 |  stream_id = "your_stream_id" # See https://plotly.com/settings
 |  py.plot(Data([Scatter(x=[], y=[],
 |                        stream=Stream(token=stream_id, maxpoints=100))]))
 |  # Strea

In [ ]:
# (@) Make instance of the `Stream link` object 
#     with the same stream id as  the `Stream Id` object
s = py.Stream(stream_id)

# (@) Open the stream
s.open()

We can now use the Stream Link object `s` in order to `stream` data to our plot. 

As an example, we will send a time stream and some random numbers(for 200 iterations):

In [10]:
# (*) Import module keep track and format current time
import datetime 
import time   
 
i = 0    # a counter
k = 5    # some shape parameter
N = 200  # number of points to be plotted

# Delay start of stream by 5 sec (time to switch tabs)
time.sleep(5) 

while i<N:
    i += 1   # add to counter
    
    # Current time on x-axis, random numbers on y-axis
    x = datetime.datetime.now().strftime('%Y-%m-%d %H:%M:%S.%f')
    y = (np.cos(k*i/50.)*np.cos(i/50.)+np.random.randn(1))[0] 
    
    # (-) Both x and y are numbers (i.e. not lists nor arrays)
    
    # (@) write to Plotly stream!
    s.write(dict(x=x, y=y))  
    
    # (!) Write numbers to stream to append current data on plot,
    #     write lists to overwrite existing data on plot (more in 7.2).
            
    time.sleep(0.08)  # (!) plot a point every 80 ms, for smoother plotting
    
# (@) Close the stream when done plotting
s.close() 

A stream of data totalling 200 points is sent to Plotly's servers in real-time. 

Watching this unfold in an opened plot.ly tab looks something like (in the old UI):

In [11]:
from IPython.display import YouTubeVideo
YouTubeVideo('OVQ2Guypp_M', width='100%', height='350')

It took Plotly around 15 seconds to plot the 200 data points sent in the data stream. After that, the generated plot looks like any other Plotly plot.

With that said, if you have enough computer resources to let a server run indefinitely, why not have 

    >>> while True: 

as the while-loop expression and never close the stream. 

Luckily, it turns out that Plotly has access to such computer resources; a simulation generated using the same code as the above has been running since March 2014.

This plot is embedded below:

In [12]:
# Embed never-ending time series streaming plot
tls.embed('streaming-demos','12')

# Note that the time point correspond to internal clock of the servers, 
# that is UTC time.

Anyone can view your streaming graph in real-time. All viewers will see the same data simultaneously (try it! Open up this notebook up in two different browser windows and observer
that the graphs are plotting identical data!).

Simply put, Plotly's streaming API is awesome!

In brief: to make a Plotly streaming plot:

1. Make a `stream id object` (`Stream` in the `plotly.graph_objs` module) containing the `stream id`(which is found in the **settings** of your Plotly account) and the maximum number of points to be keep on screen (which is optional).

2. Provide the `stream id object` as the key value for the `stream` attribute in your trace object. 

3. Make a `stream link object` (`py.Stream`) containing the same stream id as the `stream id object` and open the stream with the `.open()` method.

4. Write data to the `stream link object` with the `.write()` method. When done, close the stream with the `.close()` method.


Here are the links to the subsections' notebooks:

* [7.0 Streaming API introduction](https://plotly.com/python/intro_streaming)
* [7.1 A first Plotly streaming plot](https://plotly.com/python/streaming_part1)

<div style="float:right; \">
    <img src="http://i.imgur.com/4vwuxdJ.png" 
 align=right style="float:right; margin-left: 5px; margin-top: -10px" />
</div>

<h4>Got Questions or Feedback? </h4>

Reach us here at: <a href="https://community.plot.ly" target="_blank">Plotly Community</a>

<h4> What's going on at Plotly? </h4>
Check out our twitter: 
<a href="https://twitter.com/plotlygraphs" target="_blank">@plotlygraphs</a>



In [2]:
from IPython.display import display, HTML

display(HTML('<link href="//fonts.googleapis.com/css?family=Open+Sans:600,400,300,200|Inconsolata|Ubuntu+Mono:400,700" rel="stylesheet" type="text/css" />'))
display(HTML('<link rel="stylesheet" type="text/css" href="http://help.plot.ly/documentation/all_static/css/ipython-notebook-custom.css">'))

! pip install publisher --upgrade
import publisher
publisher.publish(
    's7_streaming_p1-first-stream', 'python/streaming_part1//', 'Getting Started with Plotly Streaming',
    'Getting Started with Plotly Streaming',
    title = 'Getting Started with Plotly Streaming',
    thumbnail='', language='python',
    layout='user-guide', has_thumbnail='false') 

Requirement already up-to-date: publisher in /Library/Frameworks/Python.framework/Versions/2.7/lib/python2.7/site-packages
